In [1]:
import pandas as pd
from IPython.display import clear_output, Markdown, Math
import ipywidgets as widgets
import os

----
## file input stuff:

* replace `test.txt` with your whatsapp log file

In [2]:
%%bash
./whatsapp2csv.sh test.txt

processing File: test.txt
successfully finished action: processing File: test.txt
Wrote output to test.txt.csv


* read table `test.csv` exported by `whatsapp2csv.sh`

In [ ]:
messages = pd.read_csv('test.txt.csv', delimiter='\t')
messages.head()

* read emoji-data (can be found here: https://www.unicode.org/Public/emoji/11.0/emoji-data.txt) and generate a table file out of it

In [4]:
%%bash
if [ ! -e emoji-data.txt ]
then
    echo "downloading emoji specification"
    wget https://www.unicode.org/Public/emoji/11.0/emoji-data.txt
else
    echo "found existing emoji specification"
fi


found existing emoji specification


In [5]:
emoji_blacklist = set([
    0x1F3FB,
    0x1F3FC,
    0x1F3FD,
    0x1F3FE,
    0x1F3FF,
    0x2642,
    0x2640
])

In [6]:
emoji_data = pd.read_csv('emoji-data.txt', delimiter=';', comment='#', names=["unicode","type"])
emoji_data['type'] = emoji_data['type'].str.strip()
emoji_data = emoji_data[emoji_data['type'] == "Emoji_Presentation"]

* now build a set out of the unicode types

In [7]:
ord("😀") == int('0x1f600',16)

True

In [8]:
emoji_codes = emoji_data['unicode']
emoji_codes.head()

228    231A..231B    
229    23E9..23EC    
230    23F0          
231    23F3          
232    25FD..25FE    
Name: unicode, dtype: object

* we have to iterate over the whole list and extract all given ranges:

In [9]:
emoji_code_list = []
for entry in emoji_codes:
    # testing whether we have an entry or a range:
    if '.' in entry:
        # range
        a,b = entry.split("..")
        for i in range(int(a,16),int(b,16) +1):
            if i not in emoji_blacklist:
                emoji_code_list.append(i)
    else:
        # single entry
        if i not in emoji_blacklist:
            emoji_code_list.append(int(entry,16))
emoji_code_set = set(emoji_code_list)
display(Markdown("**used Emojis:**"))
display("".join([chr(x) for x in emoji_code_set]))
display(Markdown("**blacklisted Emojis:**"))
display("".join([chr(x) for x in emoji_blacklist]))

**used Emojis:**

'🀄\U0001f9f1\U0001f9f2\U0001f9f3\U0001f9f4\U0001f9f5\U0001f9f6🃏🤐🤑🤒🤓🤔🤕🤖🤗🤘🤙🤚🤛🤜🤝🤞\U0001f91f🤠🤡🤢🤣🤤🤥🤦🤧\U0001f928\U0001f929\U0001f92a\U0001f92b\U0001f92c\U0001f92d\U0001f92e\U0001f92f🤰\U0001f931\U0001f932🤳🤴🤵🤶🤷🤸🤹🤺🤼🤽🤾🥀🥁🥂🥃🥄🥅🥇🥈🥉🥊🥋\U0001f94c\U0001f94d\U0001f94e\U0001f94f🥐🥑🥒🥓🥔🥕🥖🥗🥘🥙🥚🥛🥜🥝🥞\U0001f95f\U0001f960\U0001f961\U0001f962\U0001f963\U0001f964\U0001f965\U0001f966\U0001f967\U0001f968\U0001f969\U0001f96a\U0001f96b\U0001f96c\U0001f96d\U0001f96e\U0001f96f\U0001f970\U0001f9ec\U0001f9ed\U0001f973\U0001f974\U0001f975\U0001f976\U0001f9ee\U0001f97a\U0001f9ef\U0001f97c\U0001f97d\U0001f97e\U0001f97f🦀🦁🦂🦃🦄🦅🦆🦇🦈🦉🦊🦋🦌🦍🆎🦎🦏🆑🆒🆓🆔🆕🆖🆗🆘🆙🆚\U0001f992\U0001f993\U0001f994\U0001f995\U0001f996\U0001f997\U0001f998\U0001f999\U0001f99a\U0001f99b\U0001f99c\U0001f99d\U0001f99e\U0001f99f\U0001f9a0\U0001f9a1\U0001f9a2\U0001f9f8\U0001f9b0\U0001f9b1\U0001f9b2\U0001f9b3\U0001f9b4\U0001f9b5\U0001f9b6\U0001f9b7\U0001f9b8\U0001f9b9🧀\U0001f9c1\U0001f9c2\U0001f9d0\U0001f9d1\U0001f9d2\U0001f9d3\U0001f9d4\U0001f9d5\U0001f9d6\U0001f9d7\U0001f9

**blacklisted Emojis:**

'♀♂🏻🏼🏽🏾🏿'

In [10]:
# simple test:
print(ord("😀") in emoji_code_set, ord("a") in emoji_code_set)

True False


* expanding column and fill new emojis

In [11]:
messages["emojis"] = None

In [12]:
for i in messages.index:
    emoji_list = []
    m = messages.iloc[i]['message']
    m_new = ""
    for c in str(m):
        if ord(c) in emoji_code_set:
            emoji_list.append(c)
        elif ord(c) not in emoji_blacklist:
            m_new += c
            
    messages.loc[i,'emojis'] = set(emoji_list)
    #remove emiójis from message
    messages.loc[i,'message'] = m_new


In [ ]:
messages[:20]

* get a list only containing messaged with emojis

In [14]:
emoji_messages = messages[[True if len(e) > 0 else False for e in messages['emojis']]]
emoji_messages = emoji_messages[emoji_messages['message'] != ""]

In [ ]:
display(emoji_messages)

----
## learning part

In [16]:
import numpy as np
import itertools
import sklearn.utils as sku
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer, HashingVectorizer
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import MultiLabelBinarizer

In [17]:
mlb = MultiLabelBinarizer()

labels=mlb.fit_transform(emoji_messages['emojis'])

In [18]:
X1, Xt1, y1, yt1 = train_test_split(emoji_messages['message'], labels, test_size=0.1, random_state=4222)

In [19]:
vectorizer = TfidfVectorizer(stop_words='english')
vec_train = vectorizer.fit_transform(X1)
vec_test = vectorizer.transform(Xt1)

In [ ]:
from sklearn.ensemble import RandomForestClassifier as RFC
from sklearn.neural_network import MLPClassifier as MLP
from sklearn.naive_bayes import MultinomialNB as MNB
from sklearn.multiclass import OneVsRestClassifier as OVRC
#clf_a = OVRC(RFC(criterion='entropy', random_state=4222))
clf_a = OVRC(MLP(hidden_layer_sizes=(10,)))
#clf_a = OVRC(MNB())
clf_a.fit(vec_train, y1)

In [23]:
pred = clf_a.predict(vectorizer.transform(Xt1))

In [ ]:
testlist = pd.DataFrame({'message': Xt1, 'pred': mlb.inverse_transform(pred), 'teacher': mlb.inverse_transform(yt1)})
testlist.to_csv('export.csv')
testlist

In [ ]:

out = widgets.Output()

t = widgets.Text()
b = widgets.Button(
    description='get smiley',
    disabled=False,
    button_style='', # 'success', 'info', 'warning', 'danger' or ''
    tooltip='Click me',
    icon='check'
)



def handle_submit(sender):
    with out:
        clear_output()
    with out:
        display(Markdown("# " + str(mlb.inverse_transform(clf_a.predict(vectorizer.transform([t.value])))[0])))

b.on_click(handle_submit)
    
display(t)
display(widgets.VBox([b, out]))  